# Y~G ACGT Probabilities 

> 

In [ ]:
import numpy as np
import pandas as pd

# from EnvDL.core import ensure_dir_path_exists 
# from EnvDL.dlfn import g2fc_datawrapper, BigDataset, plDNN_general
# from EnvDL.dlfn import ResNet2d, BasicBlock2d
# from EnvDL.dlfn import LSUV_

import torch
import torch.nn.functional as F # F.mse_loss
from torch.utils.data import Dataset
from torch.utils.data import DataLoader
from torch import nn

import lightning.pytorch as pl
from lightning.pytorch.loggers import TensorBoardLogger

In [ ]:
from dataG2F.core import get_data; get_data()

`name` not recognized. 
Use an allowed `name` or specify the filename as a kwarg e.g. `name = '', filename = 'demo.txt'`
Allowed `name`s are:
['ACGT', 'ACGT_hilb', 'KEGG_entries', 'KEGG_slices', 'mgmtMatNames', 'mgmtMat', 'SMatNames', 'SMat', 'PlantHarvestNames', 'PlantHarvest', 'WMat', 'WMatNames', 'WMat_hilb', 'phno', 'obs_geno_lookup', 'obs_env_lookup']


# Create Holdout Set

## Hold out specific tester hybrids

In [ ]:
# make holdout sets
phno = get_data('phno')
tmp = phno.loc[:, ['Env', 'Year', 'Hybrid']]
# tmp = pd.concat([tmp, tmp.Hybrid.str.split('/', expand=True).rename(columns={0:'F', 1:'M'})], axis=1) 
tmp[['F', 'M']] = tmp['Hybrid'].str.split('/', n=1, expand=True)

In [ ]:
tmp

Env  Year             Hybrid            F      M
0       DEH1_2014  2014        M0088/LH185        M0088  LH185
1       DEH1_2014  2014        M0143/LH185        M0143  LH185
2       DEH1_2014  2014        M0003/LH185        M0003  LH185
3       DEH1_2014  2014        M0035/LH185        M0035  LH185
4       DEH1_2014  2014        M0052/LH185        M0052  LH185
...           ...   ...                ...          ...    ...
133052  WIH3_2022  2022  W10010_0337/LH244  W10010_0337  LH244
133053  WIH3_2022  2022  W10010_0346/LH244  W10010_0346  LH244
133054  WIH3_2022  2022  W10010_0358/LH244  W10010_0358  LH244
133055  WIH3_2022  2022  W10010_0381/LH244  W10010_0381  LH244
133056  WIH3_2022  2022  W10010_0452/LH244  W10010_0452  LH244

[133057 rows x 5 columns]

In [ ]:
# create a mask for parent genotype
def  mask_parent(
        df_FM = tmp, 
        holdout = 'PHZ51'
        ):
    holdout = holdout.upper()

    mask_F = tmp.F.str.upper() == holdout
    mask_M = tmp.M.str.upper() == holdout

    mask = (mask_F | mask_M)
    return mask

In [ ]:
# Here a test set is all the 20-21 testers


testers_20_21 = ['PHZ51', 'PHP02', 'PHK76']
mask = pd.concat([mask_parent(df_FM=tmp, holdout=e) for e in testers_20_21], axis=1)

# to get the union (all the test values) use sum
mask = mask.sum(axis=1)==1
# the intersect is the product across the columns. 
# this is especially useful if inverted. If all cols are non-test then the allowed training set will be returned. 
# mask.prod(axis=1)==1

# confirm that .sum gets the same result as the sum of each mask
print(mask.sum() == sum([mask_parent(df_FM=tmp, holdout=e).sum() for e in testers_20_21]) )


True


In [ ]:
# creating validation and test masks

testers_20_21 = ['PHZ51', 'PHP02', 'PHK76']
testers_18_19 = ['PHT69', 'LH195']

mask_20_21 = pd.concat([mask_parent(df_FM=tmp, holdout=e) for e in testers_20_21], axis=1).sum(axis=1)==1
mask_18_19 = pd.concat([mask_parent(df_FM=tmp, holdout=e) for e in testers_18_19], axis=1).sum(axis=1)==1

pd.DataFrame({
    'n': [e.sum() for e in [
    (~mask_20_21 & ~mask_18_19), # not tst, not val == training 1
    (~mask_20_21 &  mask_18_19), # not tst,     val == val
    (~mask_20_21),               # not tst          == training 2
    ( mask_20_21)                # tst              == test
    ]],
    'set': ['val_training', 'val_testing', 'training', 'testing']
})

n           set
0  55445  val_training
1  42046   val_testing
2  97491      training
3  35566       testing

## What about subtracting enviromental means or BLUEs?

In [ ]:

# for adjusting to environment we could use _all_ observations but ideally we will use the same set of genotypes across all observations

tmp = phno.loc[:, ['Env', 'Year', 'Hybrid']]

def minimum_hybrids_for_env(tmp = phno.loc[:, ['Env', 'Year', 'Hybrid']],
                            year = 2014):
    # Within each year what hybrids are most common?
    tmp = tmp.loc[(tmp.Year == year), ].groupby(['Env', 'Hybrid']).count().reset_index().sort_values('Year')

    all_envs = set(tmp.Env)
    # if we filter on the number of sites a hybrid is planted at, what is the largest number of sites we can ask for before we lose a location?
    # site counts for sets which contain all envs
    i = max([i for i in list(set(tmp.Year)) if len(set(tmp.loc[(tmp.Year >= i), 'Env'])) == len(all_envs)])

    before = len(set(tmp.loc[:, 'Hybrid']))
    after  = len(set(tmp.loc[(tmp.Year >= i), 'Hybrid']))
    print(f'Reducing {year} hybrids from {before} to {after} ({round(100*after/before)}%).')
    tmp = tmp.loc[(tmp.Year >= i), ['Env', 'Hybrid']].reset_index(drop=True)
    return tmp

filter_hybrids = [minimum_hybrids_for_env(tmp = phno.loc[:, ['Env', 'Year', 'Hybrid']], year = i) for i in list(set(phno.Year)) ]

Reducing 2016 hybrids from 544 to 58 (11%).
Reducing 2017 hybrids from 477 to 475 (100%).
Reducing 2018 hybrids from 1038 to 337 (32%).
Reducing 2019 hybrids from 1157 to 1103 (95%).
Reducing 2020 hybrids from 1174 to 1055 (90%).
Reducing 2021 hybrids from 1179 to 1168 (99%).
Reducing 2022 hybrids from 548 to 548 (100%).
Reducing 2014 hybrids from 850 to 163 (19%).
Reducing 2015 hybrids from 1149 to 318 (28%).


In [ ]:
filter_hybrids = pd.concat(filter_hybrids).merge(phno, how = 'left')
filter_hybrids.head()

Env            Hybrid  Year  Replicate  Block  Plot  Phno_Idx  \
0  WIH2_2016  MBNIL_B065/PHZ51  2016        1.0    1.0  39.0     37753   
1  WIH2_2016  MBNIL_B065/PHZ51  2016        2.0    2.0   7.0     38143   
2  WIH2_2016  MBNIL_B065/PHZ51  2016        2.0    2.0  14.0     38149   
3  ONH1_2016       CG119/CG108  2016        1.0    1.0  69.0     35338   
4  ONH1_2016       CG119/CG108  2016        2.0    2.0  21.0     35522   

   Env_Idx  Geno_Idx  Yield_Mg_ha  Stand_Count_plants  Pollen_DAP_days  \
0       77      2094     9.979798                73.0             59.0   
1       77      2094     7.115826                66.0             61.0   
2       77      2094     9.690223                68.0             61.0   
3       72       528    12.309941                73.0             71.0   
4       72       528    11.429282                73.0             69.0   

   Silk_DAP_days  Plant_Height_cm  Ear_Height_cm  Root_Lodging_plants  \
0           60.0            277.0          147.0                  NaN   
1           62.0            300.0          148.0                  NaN   
2           62.0            300.0          155.0                  NaN   
3           72.0            191.0          116.0                  NaN   
4           69.0            172.0           99.0                  NaN   

   Stalk_Lodging_plants  Grain_Moisture   Twt_kg_m3  
0                   NaN            18.4  803.203586  
1                  24.0            18.8  835.383217  
2                  19.0            19.5  828.947291  
3                   1.0            18.7  716.962175  
4                   NaN            19.0  711.813434

In [ ]:
# send data to R?
# filter_hybrids.loc[:, ['Yield_Mg_ha', 'Env', 'Year', 'Hybrid']].to_csv('./rm_me_test_to_r.csv')

In [ ]:
# Simplest first: Grouped means
naieve_filter_hybrids = filter_hybrids.loc[:, ['Yield_Mg_ha', 'Env', 'Year', 'Hybrid']
                                     ].groupby(['Env', 'Year']
                                     ).agg(EnvMean = ('Yield_Mg_ha', 'mean')
                                     ).reset_index()
naieve_filter_hybrids.head()

Env  Year   EnvMean
0  ARH1_2016  2016  6.831982
1  ARH1_2017  2017  6.229323
2  ARH1_2018  2018  6.315195
3  ARH2_2016  2016  1.305052
4  ARH2_2017  2017  8.991527

In [ ]:
# Slightly more complicated: OLS
import patsy
import statsmodels.api as sm
# fm = sm.OLS(
#     filter_hybrids.loc[:, 'Yield_Mg_ha'],
#     np.asarray(filter_hybrids.loc[:, 'Env'])
#     ).fit()

# print(fm.summary())


# alternate version
# from statsmodels.formula.api import ols
# model = ols("Yield_Mg_ha ~ Env", data=filter_hybrids)
# results = model.fit()

In [ ]:
# in patsy / is like * but where b is nested in a (a/b)
y, X = patsy.dmatrices("Yield_Mg_ha ~ 1 + (Year / Env) + Hybrid", filter_hybrids, return_type='matrix')

In [ ]:
fm = sm.OLS(y, X).fit()
fmr = fm.predict(X)

In [ ]:
import plotly.express as px

res = filter_hybrids.loc[:, ['Env',
 'Hybrid',
 'Year',
 'Yield_Mg_ha']].copy()

res['yhat_fm'] = fmr
res['resid_fm'] = res['yhat_fm'] - res['Yield_Mg_ha']

fig = px.scatter(res, x = 'Yield_Mg_ha', y = 'resid_fm')
fig

In [ ]:
# to confirm I can extract the effects without the influence of the hybrid I should create dmatricies for a single hybrid/env and reproduce that on my own.


# # y, X = patsy.dmatrices("Yield_Mg_ha ~ 1 + (Year / Env) + Hybrid", filter_hybrids, return_type='matrix')
# mask = ((filter_hybrids.Env == 'WIH2_2016') &
# (filter_hybrids.Year == 2016) &
# (filter_hybrids.Hybrid == 'MBNIL_B065/PHZ51'))

# fm.predict(patsy.dmatrices("Yield_Mg_ha ~ 1 + (Year / Env) + Hybrid", 
#                 filter_hybrids.loc[mask, ].loc[0, ], 
#                 return_type='matrix')[1]
# )

In [ ]:
if False:
    def _fit_mixed_model_year(year = 2014):
        tmp = filter_hybrids.loc[(filter_hybrids.Year == year),]
        # in patsy / is like * but where b is nested in a (a/b)
        y, X  = patsy.dmatrices("Yield_Mg_ha ~ 1 + Env", tmp, return_type='matrix')
        _, Xg = patsy.dmatrices("Yield_Mg_ha ~ Hybrid",  tmp, return_type='matrix')
        grouping = np.asarray(tmp.loc[:, 'Hybrid'])

        # this could take a while on the full data which is why I'm running each year as its own model
        fmm = sm.regression.mixed_linear_model.MixedLM(
            endog = np.asarray(y),
            exog  = np.asarray(X),
            # groups= np.asarray(Xg)
            groups= grouping
        ).fit()

        tmp = tmp.loc[:, ['Env', 'Yield_Mg_ha']]
        tmp.loc[:, 'blue_fmm'] = fmm.predict(exog  = np.asarray(X))
        return tmp

    fmmr = pd.concat([_fit_mixed_model_year(year = i) for i in list(set(filter_hybrids.Year))])

    res = res.merge(fmmr.loc[:, ['Env', 'blue_fmm']].drop_duplicates())
    res['resid_blue'] = res['blue_fmm'] - res['Yield_Mg_ha']

    # mse of fixed effects model is actually a little better
    print(res.loc[:, ['resid_fm', 'resid_blue']].pow(2).mean())

    fig = px.scatter(res, x = 'Yield_Mg_ha', y = 'resid_blue')
    fig

# Return to DNN

In [ ]:
from dataG2F.qol import ensure_dir_path_exists

In [ ]:
# Run settings: 
max_epoch = 2
batch_size = 24

In [ ]:
use_gpu_num = 0

device = "cuda" if torch.cuda.is_available() else "cpu"
if use_gpu_num in [0, 1]: 
    torch.cuda.set_device(use_gpu_num)
print(f"Using {device} device")

Using cuda device


In [ ]:
cache_path = '../nbs_artifacts/port02.20_g2fc_G_ACGT_FCN/'
save_prefix = [e for e in cache_path.split('/') if e != ''][-1]
ensure_dir_path_exists(dir_path = cache_path)

## Load data

In [ ]:
# get_data('ACGT')
# get_data('obs_geno_lookup').shape
# get_data(filename = 'ACGT_gene_slice_list.pkl')

In [ ]:
obs_geno_lookup = get_data('obs_geno_lookup')
phno            = get_data('phno')
ACGT            = get_data('ACGT')

In [ ]:
assert 0 == phno.loc[:, 'Yield_Mg_ha'].isna().sum()

y = phno.loc[:, 'Yield_Mg_ha']
y_c = y.mean()
y_s = y.std()

# for this test don't worry about information leakage
y = (y - y_c)/y_s

In [ ]:
# n = y.shape[0]

# idxs = torch.linspace(0, n-1, n)
# # shuffle
# idxs = idxs[torch.randperm(n)]


# use mask from above to get training set?

In [ ]:
## Suppose we wanted to convert 

xx = ACGT[0:20, :, 0:10]
# find the maximum for each position
most_common_snps     = xx.sum(axis=0).argmax(axis = 0)
most_common_snp_mask = torch.zeros(xx.shape[1:])

# loop over nucleotides dim to create a mask of the major alleles
for i in range(most_common_snp_mask.shape[0]):
    most_common_snp_mask[i, (most_common_snps == i)] = 1

# multiply by mask to get rid of non-major alleles, 
xx = 2*(torch.from_numpy(xx) * most_common_snp_mask)
xx = xx.sum(axis=1)
# xx now is major/minor allele count
(xx)

tensor([[1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [1., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [1., 2., 1., 1., 1., 1., 1., 2., 1., 1.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [2., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [2., 2., 1., 1., 1., 1., 2., 1., 2., 2.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [2., 2., 2., 2., 2., 2., 2., 1., 2., 2.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.],
        [1., 1., 2., 2., 2., 2., 1., 2., 1., 1.]],

In [ ]:
tmp = phno.loc[:, ['Env', 'Year', 'Hybrid']]
tmp[['F', 'M']] = tmp['Hybrid'].str.split('/', n=1, expand=True)

mask = pd.concat([
    mask_parent(df_FM=tmp, 
                holdout=e) for e in [
        # 2020 - 2021 testers
        'PHZ51', 
        # 'PHP02', 
        # 'PHK76'
        ] ], axis=1)

test_idx  = mask.loc[(mask[0]),  ].index
train_idx = mask.loc[(~mask[0]), ].index



In [ ]:
from EnvDL.dlfn import BigDataset, plDNN_general

In [ ]:
training_dataloader = DataLoader(BigDataset(
    lookups_are_filtered = False,
    lookup_obs  = torch.from_numpy(np.array(train_idx)), #X.get('val:train',       ops_string='   asarray from_numpy      '),
    lookup_geno = torch.from_numpy(obs_geno_lookup),
    y =           torch.from_numpy(y.to_numpy()).to(torch.float32)[:, None],
    G =           torch.from_numpy(ACGT).to(torch.float32),
    G_type = 'raw',
    send_batch_to_gpu = 'cuda:0'
    ),
    batch_size = batch_size,
    shuffle = True
)

In [ ]:
validation_dataloader = DataLoader(BigDataset(
    lookups_are_filtered = False,
    lookup_obs  = torch.from_numpy(np.array(test_idx)), #X.get('val:train',       ops_string='   asarray from_numpy      '),
    lookup_geno = torch.from_numpy(obs_geno_lookup),
    y =           torch.from_numpy(y.to_numpy()).to(torch.float32)[:, None],
    G =           torch.from_numpy(ACGT).to(torch.float32),
    G_type = 'raw',
    send_batch_to_gpu = 'cuda:0'
    ),
    batch_size = batch_size,
    shuffle = True
)

In [ ]:
# X = g2fc_datawrapper()
# X.set_split()
# X.load_all(name_list = ['obs_geno_lookup', 'YMat', 'ACGT',], store=True) 

# X.calc_cs('YMat', version = 'np', filter = 'val:train')
# X.calc_cs('ACGT',                 filter = 'val:train', filter_lookup= 'obs_geno_lookup')

In [ ]:
# training_dataloader = DataLoader(BigDataset(
#     lookups_are_filtered = False,
#     lookup_obs  = X.get('val:train',       ops_string='   asarray from_numpy      '),
#     lookup_geno = X.get('obs_geno_lookup', ops_string='   asarray from_numpy      '),
#     y =           X.get('YMat',            ops_string='cs asarray from_numpy float')[:, None],
#     G =           X.get('ACGT',            ops_string='           from_numpy float'),
#     G_type = 'raw',
#     send_batch_to_gpu = 'cuda:0'
#     ),
#     batch_size = batch_size,
#     shuffle = True
# )


# validation_dataloader = DataLoader(BigDataset(
#     lookups_are_filtered = False,
#     lookup_obs = X.get('val:test',         ops_string='   asarray from_numpy             '),
#     lookup_geno = X.get('obs_geno_lookup', ops_string='   asarray from_numpy             '),
#     y =          X.get('YMat',             ops_string='cs asarray from_numpy float')[:, None],
#     G =          X.get('ACGT',             ops_string='           from_numpy float'),
#     G_type = 'raw',
#     send_batch_to_gpu = 'cuda:0'
#     ),
#     batch_size = batch_size,
#     shuffle = False
# )

## Test Models

In [ ]:
def Linear_block(in_size, out_size, drop_pr):
            block = nn.Sequential(
                nn.Linear(in_size, out_size),
                nn.ReLU(),
                nn.Dropout(drop_pr)
            )
            return(block) 

In [ ]:
# A quirk of this is that to get only a single layer the length of the input tensor must be passed in. for 2+ I'll figure it out.
class NeuralNetwork(nn.Module):
    def __init__(self, parameterization):
        super(NeuralNetwork, self).__init__()            
        module_list = []

        max_layer = parameterization['num_layers']
        for i in range(max_layer):
            if i  == 0:
                name_in = f"in_{i+1}_of_{max_layer}"
            else:
                name_in = f"out_{i}_of_{max_layer}"
            name_out = f"out_{i+1}_of_{max_layer}"
            name_drop= f"drop_{i+1}_of_{max_layer}"

            if i == 0:
                module_list += [nn.Flatten()]
            

            module_list += [
                Linear_block(
                    in_size  = parameterization[name_in], 
                    out_size = parameterization[name_out], 
                    drop_pr  = parameterization[name_drop])]
            
            if (i+1) == max_layer:
                module_list += [nn.Linear(parameterization[name_out], 1)]
                
        self.x_network = nn.ModuleList(module_list)
        
    def forward(self, x):
        
        for mod in self.x_network:
            if mod == self.x_network[-1]:
                out = x # get the penultimate layer's outputs for later
            x = mod(x)
        
        pred = x
        return pred#, out

# model = NeuralNetwork(
#     parameterization = parameterization).to(device)

# model(next(iter(training_dataloader))[0][0:5])

In [ ]:
[e.shape for e in next(iter(training_dataloader))]

[torch.Size([24, 1]), torch.Size([24, 4, 125891])]

In [ ]:
# convenince wrapper to fill in for R's seq or x:y notation
def linrange(start, stop):
    import numpy as np
    diff = start - stop
    res = np.linspace(start, stop, abs(diff)+1).astype(int)
    return res 

### Tiny 2 layer block model

In [ ]:
layer_sizes = [256]
layer_drops = [0.1 for e in layer_sizes]

num_layers = len(layer_sizes)

params = {
    'num_layers':num_layers,
    f"in_1_of_{num_layers}": (4 * 125891)
}

for i in range(num_layers):
    params[f"out_{ i + 1}_of_{num_layers}"] = layer_sizes[i]
    params[f"drop_{ i + 1}_of_{num_layers}"] = layer_drops[i]
        

In [ ]:
model = NeuralNetwork(parameterization = params).to(device)
# model

In [ ]:
model(next(iter(training_dataloader))[1])


tensor([[-0.0665],
        [-0.0549],
        [-0.1228],
        [-0.1364],
        [ 0.0103],
        [-0.1878],
        [-0.1314],
        [-0.1280],
        [-0.1785],
        [-0.1409],
        [-0.0494],
        [-0.1072],
        [-0.0932],
        [-0.2002],
        [-0.1020],
        [-0.1133],
        [-0.1924],
        [-0.0353],
        [-0.2411],
        [-0.0107],
        [-0.1103],
        [-0.1318],
        [-0.0813],
        [-0.1143]], device='cuda:0', grad_fn=<AddmmBackward0>)

In [ ]:
# LSUV_(model, data = next(iter(training_dataloader))[1] )

In [ ]:
DNNG = plDNN_general(model)     
optimizer = DNNG.configure_optimizers()

logger = TensorBoardLogger("tb_ACGT_logs", name="g-acgt-tiny")
trainer = pl.Trainer(max_epochs=max_epoch, logger=logger)

trainer.fit(model=DNNG, train_dataloaders=training_dataloader, val_dataloaders=validation_dataloader)

/home/kickd/miniconda3/envs/fastai/lib/python3.11/site-packages/lightning/fabric/plugins/environments/slurm.py:191: PossibleUserWarning:

The `srun` command is available on your system but is not used. HINT: If your intention is to run Lightning on SLURM, prepend your python command with `srun` like so: srun python /home/kickd/miniconda3/envs/fastai/lib/python3.11/si ...

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs
You are using a CUDA device ('NVIDIA GeForce RTX 4090') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
Missing logger folder: tb_ACGT_logs/g-acgt-tiny
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name | Type   

Sanity Checking: |          | 0/? [00:00<?, ?it/s]

/home/kickd/miniconda3/envs/fastai/lib/python3.11/site-packages/lightning/pytorch/trainer/connectors/data_connector.py:492: PossibleUserWarning:

Your `val_dataloader`'s sampler has shuffling enabled, it is strongly recommended that you turn shuffling off for val/test dataloaders.

/home/kickd/miniconda3/envs/fastai/lib/python3.11/site-packages/lightning/pytorch/trainer/connectors/data_connector.py:441: PossibleUserWarning:

The 'val_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=31` in the `DataLoader` to improve performance.

/home/kickd/miniconda3/envs/fastai/lib/python3.11/site-packages/lightning/pytorch/trainer/connectors/data_connector.py:441: PossibleUserWarning:

The 'train_dataloader' does not have many workers which may be a bottleneck. Consider increasing the value of the `num_workers` argument` to `num_workers=31` in the `DataLoader` to improve performance.



Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_epochs=2` reached.


### Deeper linear block model

In [ ]:
            # [2048, 1024, 512, 256, 128, 64, 32, 16]
layer_sizes = [int(2**i) for i in linrange(start = 11, stop = 4)]
layer_drops = [0.1 for e in layer_sizes]

num_layers = len(layer_sizes)

params = {
    'num_layers':num_layers,
    f"in_1_of_{num_layers}": (4 * 125891)
}

for i in range(num_layers):
    params[f"out_{ i + 1}_of_{num_layers}"] = layer_sizes[i]
    params[f"drop_{ i + 1}_of_{num_layers}"] = layer_drops[i]
        

In [ ]:
model = NeuralNetwork(parameterization = params).to(device)
# model
# model(next(iter(training_dataloader))[1])

LSUV_(model, data = next(iter(training_dataloader))[1] )

In [ ]:
DNNG = plDNN_general(model)     
optimizer = DNNG.configure_optimizers()

logger = TensorBoardLogger("tb_ACGT_logs", name="g-acgt-fcn")
trainer = pl.Trainer(max_epochs=max_epoch, logger=logger)

trainer.fit(model=DNNG, train_dataloaders=training_dataloader, val_dataloaders=validation_dataloader)

In [ ]:
# torch.save(DNNG.mod, cache_path+'g-acgt-fcn'+'.pt')
import time
save_time = time.strftime("%Y-%m-%d-%H-%M-%S", time.localtime())

pt_path = cache_path+''.join([save_prefix,'__'+save_time,'.pt'])

torch.save(DNNG.mod, pt_path)

In [ ]:
# os._exit(00)